In [22]:
import numpy as np
import pandas as pd
from statsmodels.tsa.arima.model import ARIMA
#from statsmodels.tsa.statespace.varmax import VARMAX
import statsmodels.api as sm
#from statsmodels.tsa.statespace.sarimax import SARIMAX
from tqdm import tqdm
import warnings
warnings.filterwarnings("ignore")

In [2]:
x_train = pd.read_csv('./x_train.csv', index_col='ID').fillna(0)
y_train = pd.read_csv('./y_train.csv', index_col='ID').fillna(0)
train = pd.concat([x_train, y_train], axis=1).fillna(0)
test = pd.read_csv('./x_test.csv', index_col='ID').fillna(0)

In [3]:
ret_cols = [col for col in x_train.columns if 'RET' in col]
vol_cols = [col for col in x_train.columns if 'VOLUME' in col]

df = x_train[x_train['DATE']==0]


total_size = len(df)
#models = {}

model_order = (0, 0, 1) 

In [7]:
ii = 0
prediction=[]
for idx in tqdm(range(total_size)):
    stock_data = df[ret_cols].iloc[ii].values
    vol_data = df[vol_cols].iloc[ii].values

    norm_ret = (stock_data-np.mean(stock_data))/np.std(stock_data)

    if np.std(vol_data) != 0:
        norm_vol = (vol_data-np.mean(vol_data))/np.std(vol_data)
    else:
        norm_vol = vol_data
    norm_ret = stock_data
    norm_vol = vol_data
    
    model_ret = ARIMA(norm_ret, order=model_order,exog=norm_vol)
    model_vol = ARIMA(norm_vol, order=model_order)
        #model_fit = model.fit()
        
    pred = model_ret.fit().forecast(1,exog=model_vol.fit().forecast(1))

    pred *= np.std(stock_data)
    pred += np.mean(stock_data)
        
    prediction+=[pred]
    ii+=1

100%|███████████████████████████████████████| 2377/2377 [01:39<00:00, 23.98it/s]


In [8]:
df_test = y_train[x_train['DATE']==0]

In [9]:
acc = 0
for jj in range(total_size):
    pred = False
    if prediction[jj] > 0:
        pred = True
    else:
        pred = False
    if df_test.iloc[jj].values[0] == pred:
        acc +=1
acc/=total_size
print(acc*100)

52.16659655027346


Normalizing volume and returns data, with AR(1) model on DATE=0 dataset, I got 51.956% accuracy

Without normalization, I got 52.040%

On the full dataset, without normalization 49.949%

In [40]:
ii = 0
prediction=[]
for idx in tqdm(range(total_size)):
    stock_data = df[ret_cols].iloc[ii].values
    vol_data = df[vol_cols].iloc[ii].values

    norm_ret = (stock_data-np.mean(stock_data))/np.std(stock_data)

    if np.std(vol_data) != 0:
        norm_vol = (vol_data-np.mean(vol_data))/np.std(vol_data)
    else:
        norm_vol = vol_data
    norm_ret = stock_data
    norm_vol = vol_data
    
    #model_ret = ARIMA(norm_ret, order=model_order,exog=norm_vol)
    #model_vol = ARIMA(norm_vol, order=model_order)
    try:
        model = sm.tsa.VARMAX(np.array([norm_ret,norm_vol]).T,order = (1,1))
        pred = model.fit().forecast(1)[0,0]
    except:
        model = ARIMA(norm_ret, order=model_order)
        pred = model.fit().forecast(1)
        #model_fit = model.fit()
        
    

    pred *= np.std(stock_data)
    pred += np.mean(stock_data)
        
    prediction+=[pred]
    ii+=1

  0%|                                                  | 0/2377 [00:00<?, ?it/s] This problem is unconstrained.


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           13     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f= -2.40860D-01    |proj g|=  1.95205D+00

At iterate    5    f= -2.43767D-01    |proj g|=  1.34698D+00

At iterate   10    f= -2.66027D-01    |proj g|=  1.26161D+00

At iterate   15    f= -2.70318D-01    |proj g|=  5.84800D-01

At iterate   20    f= -2.83278D-01    |proj g|=  3.61541D+00

At iterate   25    f= -2.85267D-01    |proj g|=  7.38276D-01

At iterate   30    f= -2.98913D-01    |proj g|=  2.21313D+00

At iterate   35    f= -3.15681D-01    |proj g|=  2.72578D-01

At iterate   40    f= -3.19394D-01    |proj g|=  1.72087D+00


  0%|                                          | 1/2377 [00:00<10:05,  3.92it/s]


At iterate   45    f= -3.33046D-01    |proj g|=  6.31546D-01

At iterate   50    f= -3.34588D-01    |proj g|=  6.05428D-01

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   13     50     55      1     0     0   6.054D-01  -3.346D-01
  F = -0.33458827173556110     

STOP: TOTAL NO. of ITERATIONS REACHED LIMIT                 
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           13     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f= -2.39786D+00    |proj g|=  6.50382D+00

At iterate    5    f= -2.40970D+00    |proj g|=  2.89408D+00

At iter

 This problem is unconstrained.
  0%|                                          | 3/2377 [00:00<05:52,  6.73it/s]

...


At iterate   35    f= -9.64635D-01    |proj g|=  7.65998D-02

At iterate   40    f= -9.66446D-01    |proj g|=  8.84034D-02

At iterate   45    f= -9.66961D-01    |proj g|=  5.07616D-02

At iterate   50    f= -9.70701D-01    |proj g|=  1.05526D+00

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   13     50     57      1     0     0   1.055D+00  -9.707D-01
  F = -0.97070129438390984     

STOP: TOTAL NO. of ITERATIONS REACHED LIMIT                 
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           13     M =           10

At X0         0 variables are exactly at the bounds

At iter

100%|██████████████████████████████████████▉| 2376/2377 [08:35<00:00,  4.81it/s]


At iterate   35    f= -1.40107D+00    |proj g|=  1.95681D-01

At iterate   40    f= -1.40241D+00    |proj g|=  2.05392D-01

At iterate   45    f= -1.40651D+00    |proj g|=  6.66784D-01

At iterate   50    f= -1.41237D+00    |proj g|=  1.73104D+00

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   13     50     58      1     0     0   1.731D+00  -1.412D+00
  F =  -1.4123746811849369     

STOP: TOTAL NO. of ITERATIONS REACHED LIMIT                 
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           13     M =           10

At X0         0 variables are exactly at the bounds

At iter

 This problem is unconstrained.
100%|███████████████████████████████████████| 2377/2377 [08:35<00:00,  4.61it/s]


At iterate   35    f= -1.64147D+00    |proj g|=  2.07820D-01

At iterate   40    f= -1.64341D+00    |proj g|=  1.28993D+00

At iterate   45    f= -1.65953D+00    |proj g|=  4.73221D+00

At iterate   50    f= -1.66873D+00    |proj g|=  3.70442D+00

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   13     50     60      1     0     0   3.704D+00  -1.669D+00
  F =  -1.6687319942838350     

STOP: TOTAL NO. of ITERATIONS REACHED LIMIT                 


In [42]:
acc = 0
for jj in range(total_size):
    pred = False
    if prediction[jj] > 0:
        pred = True
    else:
        pred = False
    if df_test.iloc[jj].values[0] == pred:
        acc +=1
acc/=total_size
print(acc*100)

52.33487589398401
